In [130]:
run example.py

Exception ignored in: <bound method DMatrix.__del__ of <xgboost.core.DMatrix object at 0x7efc3d69aa58>>
Traceback (most recent call last):
  File "/usr/lib/python3.6/site-packages/xgboost/core.py", line 324, in __del__
    _check_call(_LIB.XGDMatrixFree(self.handle))
AttributeError: 'DMatrix' object has no attribute 'handle'


Error reading  ./recipes/8000.mmf , skipping.
there are 122135 unique ingredients out of 646431
Most common ingredients:
 [array(['salt'], 
      dtype='<U61'), array(['sugar'], 
      dtype='<U61'), array(['_chopped'], 
      dtype='<U61'), array(['water'], 
      dtype='<U61'), array(['butter'], 
      dtype='<U61'), array(['flour'], 
      dtype='<U61'), array(['eggs'], 
      dtype='<U61'), array(['onion'], 
      dtype='<U61'), array(['_minced'], 
      dtype='<U61'), array(['milk'], 
      dtype='<U61'), array(['pepper'], 
      dtype='<U61'), array(['olive_oil'], 
      dtype='<U61'), array(['_sliced'], 
      dtype='<U61'), array(['lemon_juice'], 
      dtype='<U61'), array(['egg'], 
      dtype='<U61'), array(['baking_powder'], 
      dtype='<U61'), array(['vanilla'], 
      dtype='<U61'), array(['vegetable_oil'], 
      dtype='<U61'), array(['_diced'], 
      dtype='<U61'), array(['oil'], 
      dtype='<U61'), array(['purpose_flour'], 
      dtype='<U61'), array(['baking_soda

there are 1940 unique categories out of 137600
Most common categories: [array(['dish'], 
      dtype='<U11'), array(['desserts'], 
      dtype='<U11'), array(['vegetables'], 
      dtype='<U11'), array(['breads'], 
      dtype='<U11'), array(['appetizers'], 
      dtype='<U11'), array(['poultry'], 
      dtype='<U11'), array(['meats'], 
      dtype='<U11'), array(['cakes'], 
      dtype='<U11'), array(['vegetarian'], 
      dtype='<U11'), array(['sauces'], 
      dtype='<U11'), array(['salads'], 
      dtype='<U11'), array(['soups'], 
      dtype='<U11'), array(['cookies'], 
      dtype='<U11'), array(['seafood'], 
      dtype='<U11'), array(['pasta'], 
      dtype='<U11'), array(['fruits'], 
      dtype='<U11'), array(['beef'], 
      dtype='<U11'), array(['fish'], 
      dtype='<U11'), array(['italian'], 
      dtype='<U11'), array(['mexican'], 
      dtype='<U11'), array(['pies'], 
      dtype='<U11'), array(['chinese'], 
      dtype='<U11'), array(['chocolate'], 
      dtype='<U11'

In [4]:
import pandas as pd
import xgboost as xgb

/usr/lib/python3.6/site-packages/sklearn/cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [5]:
categories[0]

['Desserts', 'Chocolate']

In [6]:
dishes = ['beans', 
 'beef', 
 'alcohol', 
 'biscuits', 
 'bread', 
 'brownies', 
 'burgers', 
 'cake', 
 'candy', 
 'caribou', 
 'casserole', 
 'cheese', 
 'cheesecake', 
 'chicken', 
 'chili', 
 'chocolate', 
 'chopmeat', 
 'cocktails', 
 'coffee', 
 'cookies', 
 'corn', 
 'crackers', 
 'cream', 
 'curry', 
 'dough', 
 'dressing', 
 'drink', 
 'eggs', 
 'fish', 
 'flowers', 
 'frostings', 
 'fruit', 
 'gin', 
 'godiva', 
 'grains', 
 'gravy', 
 'groundmeat', 
 'ham', 
 'hamburger', 
 'icings', 
 'jam', 
 'jello', 
 'jelly', 
 'lamb', 
 'marinade', 
 'muffins', 
 'mushrooms', 
 'mutton', 
 'nuts', 
 'pancakes', 
 'pasta', 
 'pastanoodle', 
 'pastries', 
 'peppers', 
 'pie', 
 'pizza', 
 'pork', 
 'potato', 
 'poultry', 
 'preserves', 
 'pudding', 
 'relishes', 
 'rice', 
 'roast', 
 'salad', 
 'salsa', 
 'sandwich', 
 'sausage', 
 'shellfish', 
 'shrimp', 
 'soup', 
 'sourdough', 
 'steak', 
 'stew', 
 'stuffing', 
 'tofu', 
 'tomatoes', 
 'tuna', 
 'turkey', 
 'veal', 
 'venison', 
 'vodka', 
 'wine', 
 'wok',]


In [7]:
ethnicities = ['african', 
 'american', 
 'appetizers', 
 'asian', 
 'australian', 
 'barbeque', 
 'beers', 
 'bengali', 
 'beverages', 
 'breakfast', 
 'british', 
 'brunch', 
 'cajun', 
 'caribbean', 
 'chinese', 
 'christmas', 
 'cuban', 
 'dairy', 
 'dessert', 
 'english', 
 'entree', 
 'family', 
 'filipino', 
 'france', 
 'french', 
 'german', 
 'greek', 
 'hawaiian', 
 'healthy', 
 'holiday', 
 'hungarian', 
 'indian', 
 'indonesian', 
 'irish', 
 'italian', 
 'japanese', 
 'korean', 
 'kosher', 
 'mexican', 
 'moroccan', 
 'norwegian', 
 'oriental', 
 'polish', 
 'seafood', 
 'southern', 
 'spanish', 
 'swedish', 
 'swiss', 
 'thai', 
 'turkish', 
 'ukrainian', 
 'vegan', 
 'vegetarian', 
 'vietnamese', 
 'welsh',]


In [8]:
# the X
dish_one_hot = np.zeros(shape=(len(recipes), len(dishes)))

# the Y
ethnicity_one_hot = np.zeros(shape=(len(recipes), len(ethnicities) + 1)) # extra column for n/a

ethnicity_classes = np.zeros(shape=(len(recipes), 1))

In [9]:
for recipeIdx, recipeCats in enumerate(categories):
    # recipeCats = all categories that the current recipe is in
    print(recipeIdx)
#     print(recipeCats)
        
    # check each recipeCat against dishes
    dishMatched = False
    for recipeCat in recipeCats:
        # check this recipe against each dish
        recipeCat = recipeCat.lower().rstrip('s')
#         print(recipeCat)
        for d, dish in enumerate(dishes):
            if dish == recipeCat:
#                 print("dish match: " + dish)
                dish_one_hot[recipeIdx][d] = 1
                dishMatched = True
    # if no dish matched, discard this
    if not dishMatched:
        print("Discarding, no dishes matched")
        dish_one_hot = np.delete(dish_one_hot, (recipeIdx), axis=0)
        ethnicity_one_hot = np.delete(ethnicity_one_hot, (recipeIdx), axis=0)
        ethnicity_classes = np.delete(ethnicity_classes, (recipeIdx), axis=0)
    # otherwise, one-hot encode the ethnicity as well
    if dishMatched:
        print("Recipe matched at least one dish.")
        ethMatched = False
        for recipeCat in recipeCats:
            recipeCat = recipeCat.lower().rstrip('s')
            for e, ethnicty in enumerate(ethnicities):
                if ethnicty == recipeCat:
#                     print("eth match: " + ethnicty)
                    ethnicity_one_hot[recipeIdx][e] = 1
                    ethnicity_classes[recipeIdx] = e
                    ethMatched = True
        if ethMatched:
            print("Recipe matched at least one ethnicity.")
        if not ethMatched:
            print("Recipe did not match any ethnicity.")
            ethnicity_one_hot[recipeIdx][len(ethnicities)] = 1 # the last column is the "none" column
            ethnicity_classes[recipeIdx] = len(ethnicities)
        
        print("Used ethnicity " + str(ethnicity_classes[recipeIdx]))

0
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 18.]
1
Discarding, no dishes matched
2
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 18.]
3
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 18.]
4
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
5
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 18.]
6
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
7
Discarding, no dishes matched
8
Discarding, no dishes matched
9
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
10
Discarding, no dishes matched
11
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
12
Discarding, no dishes matched
13
Discarding, no dishes matched
14
Recipe matched at least one dish.
Rec

133
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
134
Discarding, no dishes matched
135
Discarding, no dishes matched
136
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
137
Discarding, no dishes matched
138
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
139
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
140
Discarding, no dishes matched
141
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 18.]
142
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
143
Discarding, no dishes matched
144
Discarding, no dishes matched
145
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
146
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 38.]
147
Recipe matched at 

280
Discarding, no dishes matched
281
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
282
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
283
Discarding, no dishes matched
284
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
285
Discarding, no dishes matched
286
Discarding, no dishes matched
287
Discarding, no dishes matched
288
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
289
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
290
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
291
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
292
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
293
Recipe matched at least one dish.
Recipe did not match any

507
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
508
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
509
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
510
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 38.]
511
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
512
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 12.]
513
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 29.]
514
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 29.]
515
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
516
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
517
Recipe matched at least 

Used ethnicity [ 55.]
626
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
627
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 43.]
628
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 34.]
629
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 34.]
630
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 34.]
631
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
632
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
633
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
634
Discarding, no dishes matched
635
Discarding, no dishes matched
636
Discarding, no dishes matched
637
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 38

...

44376
Discarding, no dishes matched
44377
Discarding, no dishes matched
44378
Discarding, no dishes matched
44379
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 38.]
44380
Discarding, no dishes matched
44381
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44382
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44383
Discarding, no dishes matched
44384
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44385
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44386
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 30.]
44387
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 30.]
44388
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44389
Discarding, no dishes

44519
Discarding, no dishes matched
44520
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44521
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44522
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44523
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44524
Discarding, no dishes matched
44525
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44526
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44527
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 34.]
44528
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44529
Discarding, no dishes matched
44530
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44531
R

44675
Discarding, no dishes matched
44676
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44677
Discarding, no dishes matched
44678
Discarding, no dishes matched
44679
Discarding, no dishes matched
44680
Discarding, no dishes matched
44681
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44682
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44683
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44684
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 38.]
44685
Recipe matched at least one dish.
Recipe did not match any ethnicity.
Used ethnicity [ 55.]
44686
Discarding, no dishes matched
44687
Discarding, no dishes matched
44688
Discarding, no dishes matched
44689
Discarding, no dishes matched
44690
Discarding, no dishes matched
44691
Discarding, no dishes matched
44692
Discard

44810
Recipe matched at least one dish.
Recipe matched at least one ethnicity.
Used ethnicity [ 31.]
44811
Discarding, no dishes matched
44812
Discarding, no dishes matched
44813
Discarding, no dishes matched
44814


IndexError: index 44814 is out of bounds for axis 0 with size 44814

In [131]:
np.shape(dish_one_hot)

(44814, 84)

In [132]:
np.shape(ethnicity_one_hot)

(44814, 56)

In [133]:
np.shape(ethnicity_classes)

(44814, 1)

In [148]:
for i in range(0, len(dishes)):
    print(str(i) + dishes[i])

0beans
1beef
2alcohol
3biscuits
4bread
5brownies
6burgers
7cake
8candy
9caribou
10casserole
11cheese
12cheesecake
13chicken
14chili
15chocolate
16chopmeat
17cocktails
18coffee
19cookies
20corn
21crackers
22cream
23curry
24dough
25dressing
26drink
27eggs
28fish
29flowers
30frostings
31fruit
32gin
33godiva
34grains
35gravy
36groundmeat
37ham
38hamburger
39icings
40jam
41jello
42jelly
43lamb
44marinade
45muffins
46mushrooms
47mutton
48nuts
49pancakes
50pasta
51pastanoodle
52pastries
53peppers
54pie
55pizza
56pork
57potato
58poultry
59preserves
60pudding
61relishes
62rice
63roast
64salad
65salsa
66sandwich
67sausage
68shellfish
69shrimp
70soup
71sourdough
72steak
73stew
74stuffing
75tofu
76tomatoes
77tuna
78turkey
79veal
80venison
81vodka
82wine
83wok


In [134]:
split = 21000
dish_train = dish_one_hot[:split]
dish_test = dish_one_hot[split:]
ethnicity_train = ethnicity_one_hot[:split]
ethnicity_test = ethnicity_one_hot[split:]
ethnicity_class_train = ethnicity_classes[:split]
ethnicity_class_test = ethnicity_classes[split:]

In [135]:
np.where(ethnicity_test[:,34] == 1)

(array([   83,   278,   478,   483,   484,   489,   490,   491,   494,
          495,   496,   497,   500,   503,   504,   507,   509,   510,
          511,   521,   527,   532,   534,   545,   548,   559,   586,
          594,   601,   604,   605,   607,   610,   620,   628,   630,
          897,  1139,  1472,  1479,  1528,  1645,  1647,  1648,  1649,
         1651,  1652,  1678,  1679,  1680,  1771,  1794,  1913,  2015,
         2161,  2303,  2374,  2453,  2457,  2543,  2668,  2674,  3202,
         3341,  3578,  3579,  3667,  3705,  3717,  3776,  3791,  3810,
         4160,  4220,  4413,  4447,  4503,  4505,  4506,  4507,  4622,
         4648,  4978,  4990,  4992,  5042,  5047,  5048,  5049,  5055,
         5075,  5083,  5096,  5129,  5155,  5171,  5258,  5390,  5452,
         5484,  5522,  5610,  5770,  5860,  5926,  6005,  6049,  6083,
         6353,  6579,  6951,  7248,  7401,  7431,  7534,  7535,  7537,
         7538,  7541,  7546,  7553,  7563,  7571,  7577,  7582,  7584,
      

In [136]:
np.shape(ethnicity_class_train)

(21000, 1)

In [139]:
xg_train = xgb.DMatrix(dish_train, label=ethnicity_train[:,34])
xg_test = xgb.DMatrix(dish_test, label=ethnicity_test[:,34])
param = {}
param['objective'] = 'binary:logistic'
param['eta'] = 0.1
param['max_depth'] = 6
param['silent'] = 1
param['nthread'] = 4
# param['num_class'] = 2
num_round = 10
watchlist = [ (xg_train,'train'), (xg_test, 'test') ]
bst = xgb.train(param, xg_train, num_round, watchlist );
# get prediction
pred = bst.predict( xg_test );

[0]	train-error:0.015095	test-error:0.016041
[1]	train-error:0.015095	test-error:0.016041
[2]	train-error:0.015095	test-error:0.016041
[3]	train-error:0.015095	test-error:0.016041
[4]	train-error:0.015095	test-error:0.016041
[5]	train-error:0.015095	test-error:0.016041
[6]	train-error:0.015095	test-error:0.016041
[7]	train-error:0.015095	test-error:0.016041
[8]	train-error:0.015095	test-error:0.016041
[9]	train-error:0.015048	test-error:0.016167


In [142]:
pred
for i in pred:
    print(i)

0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.221125
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.305923
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.1

0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.221125
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.221125
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.305923
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.231936
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.305923
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.310329
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.310329
0.184447
0.184447
0.184447

0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.221125
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.221125
0.184447
0.184447
0.221125
0.305923
0.184447
0.221125
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.19097
0.184447
0.19097
0.19097
0.19097
0.19097
0.19097
0.19097
0.19097
0.19097
0.184447
0.184447
0.19097
0.19097
0.19097
0.19097
0.19097
0.184447
0.19097
0.19097
0.19097
0.19097
0.184447
0.19097
0.19097
0.19097
0.19097
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.221125
0.19097
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.

0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.19097
0.184447
0.19097
0.184447
0.221125
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.305923
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.305923
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.305923
0.184447
0.270408
0.184447
0.19097
0

0.184447
0.184447
0.184447
0.184447
0.184447
0.221125
0.184447
0.184447
0.184447
0.184447
0.19097
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.221125
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.18

0.184447
0.184447
0.184447
0.184447
0.184447
0.292956
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.1

0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.292956
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.292956
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.19097
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.1

0.184447
0.184447
0.305923
0.305923
0.305923
0.184447
0.184447
0.184447
0.305923
0.305923
0.305923
0.184447
0.292956
0.184447
0.305923
0.305923
0.184447
0.184447
0.184447
0.235268
0.305923
0.305923
0.305923
0.305923
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.270408
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.221125
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.184447
0.184447
0.305923
0.305923
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.305923
0.184447
0.184447
0.184447
0.184447
0.184447
0.19097
0.184447
0.305923
0.184447
0.184447
0.184447
0.184447
0.235356
0.19097
0.184447
0.19097
0.184447
0.184447
0.184447
0.305923
0.221125
0.305923
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.184447
0.221125
0.184

In [141]:
xgb_classif = xgb.XGBClassifier()
xgb_classif.fit(dish_train, ethnicity_train[:,34], eval_metric='auc')

XGBClassifier(base_score=0.5, colsample_bylevel=1, colsample_bytree=1,
       gamma=0, learning_rate=0.1, max_delta_step=0, max_depth=3,
       min_child_weight=1, missing=None, n_estimators=100, nthread=-1,
       objective='binary:logistic', reg_alpha=0, reg_lambda=1,
       scale_pos_weight=1, seed=0, silent=True, subsample=1)

In [122]:
xgb_classif_pred = xgb_classif.predict_proba(dish_test)
xgb_classif_pred[:,1]

array([ 0.00709762,  0.00709762,  0.00709762, ...,  0.00709762,
        0.00709762,  0.00709762], dtype=float32)

In [129]:
xgb_classif_pred[83][1]

0.017269455

In [150]:
np_pizza = np.zeros(shape=(86,))
np_pizza[55] = 1
np_pizza

array([ 0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  1.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,
        0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.])

In [153]:
xgb_classif.predict_proba([np_pizza])

ValueError: feature_names mismatch: ['f0', 'f1', 'f2', 'f3', 'f4', 'f5', 'f6', 'f7', 'f8', 'f9', 'f10', 'f11', 'f12', 'f13', 'f14', 'f15', 'f16', 'f17', 'f18', 'f19', 'f20', 'f21', 'f22', 'f23', 'f24', 'f25', 'f26', 'f27', 'f28', 'f29', 'f30', 'f31', 'f32', 'f33', 'f34', 'f35', 'f36', 'f37', 'f38', 'f39', 'f40', 'f41', 'f42', 'f43', 'f44', 'f45', 'f46', 'f47', 'f48', 'f49', 'f50', 'f51', 'f52', 'f53', 'f54', 'f55', 'f56', 'f57', 'f58', 'f59', 'f60', 'f61', 'f62', 'f63', 'f64', 'f65', 'f66', 'f67', 'f68', 'f69', 'f70', 'f71', 'f72', 'f73', 'f74', 'f75', 'f76', 'f77', 'f78', 'f79', 'f80', 'f81', 'f82', 'f83'] ['f0', 'f1', 'f2', 'f3', 'f4', 'f5', 'f6', 'f7', 'f8', 'f9', 'f10', 'f11', 'f12', 'f13', 'f14', 'f15', 'f16', 'f17', 'f18', 'f19', 'f20', 'f21', 'f22', 'f23', 'f24', 'f25', 'f26', 'f27', 'f28', 'f29', 'f30', 'f31', 'f32', 'f33', 'f34', 'f35', 'f36', 'f37', 'f38', 'f39', 'f40', 'f41', 'f42', 'f43', 'f44', 'f45', 'f46', 'f47', 'f48', 'f49', 'f50', 'f51', 'f52', 'f53', 'f54', 'f55']
ex